In [1]:
import os
import numpy as np
from sklearn.metrics import accuracy_score
from skimage import io
from skimage.measure import moments, moments_central, moments_normalized, moments_hu
from skimage.color import rgb2gray
from skimage.filters import threshold_otsu

In [2]:
# Function to extract features
def extract_features(dir_path, identifier):
    # Read image from file_path
    img = io.imread(os.path.join(dir_path, identifier + ".png"))
    img = rgb2gray(img)
    threshold = threshold_otsu(img)
    # Binarize image
    img_binary = (img > threshold)
    # Plot image
    
    # Initialize feature list
    hu_features = []
    mu_features = []
    nu_features = []
    class_ids = []
    # Identify regions of interest from labelled image

    # Determine the bounding boxes for each region of interest
    regions = []
    with open(os.path.join(dir_path, identifier + ".gt_data.txt")) as fp:
        lines = fp.readlines()
        for line in lines:
            minr, minc, maxr, maxc = line.split(" ")[:4]
            minr, minc, maxr, maxc = int(minr), int(minc), int(maxr), int(maxc)
            class_id = line.split(" ")[4]
            regions.append([(minr, minc, maxr, maxc), class_id]) 
    for region in regions:
        minr, minc, maxr, maxc = region[0]
        class_ids.append(region[1])
        
        roi = img_binary[minr:maxr, minc:maxc]
        m = moments(roi)
        cr = m[0, 1] / m[0, 0]
        cc = m[1, 0] / m[0, 0]
        center = (cr, cc)
        #center = ((minr + maxr) // 2, (minc + maxc) // 2)
        mu = moments_central(roi, center)
        mu_features.append([i for sub in mu for i in sub])
        nu = moments_normalized(mu)
        nu_features.append([i for sub in nu for i in sub])
        #print(nu)
        # Compute Hu Moments
        hu = moments_hu(nu)
        # Append Hu moments to features list
        hu_features.append(hu)
    return class_ids, hu_features, mu_features, nu_features

In [3]:
def get_file_identifiers(dir_path):
    identifiers = set()
    for _, _, files in os.walk(dir_path):
            for file_name in files:
                if file_name.endswith(".txt"):
                    identifiers.add(file_name.split(".")[0])
    return identifiers

In [4]:
yolo_result_dir = "./yolo_result"
identifier_dict = {}
train_dir_path = os.path.join(yolo_result_dir, "train")
val_dir_path = os.path.join(yolo_result_dir, "val")
test_dir_path = os.path.join(yolo_result_dir, "test")
identifier_dict["train"] = get_file_identifiers(train_dir_path)
identifier_dict["val"] = get_file_identifiers(val_dir_path)
identifier_dict["test"] = get_file_identifiers(test_dir_path)

In [5]:
# Create feature dictionary
def get_feature_dict(data_dir, data_split):
    # Dictionary to store training data features
    hu_feature_dict = {}
    #mu_feature_dict = {}
    nu_feature_dict = {}
    #bounding_boxes = []
    for dir_path, _, files in os.walk(data_dir):
        for file_name in files:
            if file_name.endswith(".gt_data.txt"):
                identifier = file_name.split(".")[0]
                if identifier in identifier_dict.get(data_split):
                    #file_path = os.path.join(directory, file_name)
                    class_ids, hu_features, mu_features, nu_features = extract_features(dir_path, identifier)
                    for class_id in class_ids:
                        hu_feature_dict[class_id] = hu_feature_dict.get(class_id, []) + hu_features
                        #mu_feature_dict[class_id] = mu_feature_dict.get(class_id, []) + mu_features
                        nu_feature_dict[class_id] = nu_feature_dict.get(class_id, []) + nu_features
        #boxes, hu_feature_dict[char_label], mu_feature_dict[char_label], nu_feature_dict[char_label] = extract_features(file_path, show_plots)
        #bounding_boxes.extend(boxes)
    
    return hu_feature_dict, nu_feature_dict

In [6]:
def get_bbox_annotation(yolo_annotation, width, height):
    x, y, w, h = yolo_annotation
    x, y, w, h = float(x) * width, float(y) * height, float(w) * width, float(h) * height
    x1, y1 = x - w/2, y - h/2
    x2, y2 = x + w/2, y + h/2
    return int(x1), int(y1), int(x2), int(y2)

In [7]:
def extract_pred_features(dir_path, identifier):
    #print(dir_path, identifier)
    # Read image from file_path
    img = io.imread(os.path.join(dir_path, identifier + ".png"))
    img = rgb2gray(img)
    threshold = threshold_otsu(img)
    # Binarize image
    img_binary = (img > threshold)
    width, height = img_binary.shape
    #print(width, height)
    # Initialize feature list
    #hu_features = []
    features = []
    #nu_features = []
    regions = []
    with open(os.path.join(dir_path, identifier + ".txt")) as fp:
        lines = fp.readlines()
        for line in lines:
            yolo_annotation = line.strip().split(" ")[1:]
            minr, minc, maxr, maxc = get_bbox_annotation(yolo_annotation, width, height)
            #print(minr, minc, maxr, maxc)
            
            regions.append((minr, minc, maxr, maxc)) 
    #print(regions)
    for region in regions:
        minr, minc, maxr, maxc = region
        # Identify regions of interest
        roi = img_binary[minr:maxr, minc:maxc]
        m = moments(roi)
        cr = m[0, 1] / m[0, 0]
        cc = m[1, 0] / m[0, 0]
        center = (cr, cc)
        #center = ((minr + maxr) // 2, (minc + maxc) // 2)
        mu = moments_central(roi, center)
        #mu_features.append([i for sub in mu for i in sub])
        nu = moments_normalized(mu)
        #nu_features.append([i for sub in nu for i in sub])
        #print(nu)
        # Compute Hu Moments
        hu = moments_hu(nu)
        # Append Hu moments to features list
        #hu_features.append(hu)
        features.append(list(hu) + [i for sub in nu for i in sub])
    return features

In [8]:
def get_predicted_features(dir_path, data_split):
    id_feature_dict = {}
    feature_id_dict = {}
    for id in identifier_dict.get(data_split):
        features = extract_pred_features(os.path.join(dir_path, data_split), id)
        id_feature_dict[id] = features
        #feature_id_dict[features] = id
    return id_feature_dict

In [10]:
# For training

# Location for training data
data_dir = "./"
train_hu_feature_dict, train_nu_feature_dict = get_feature_dict(data_dir, "train")

# For validation / testing:
pred_feature_dict = get_predicted_features(yolo_result_dir, "test")
#pred_feature_dict["val"] = get_predicted_features(yolo_result_dir, "val")
#pred_feature_dict["test"] = get_predicted_features(yolo_result_dir, "test")
# Get normalized feature dict
#normalized_hu_feature_dict = normalize(hu_feature_dict, mean, variance)
# Get flat 2-D feature list for training
#flat_feat_list = get_flat_feature_list(normalized_hu_feature_dict)
# Get index-label mapping
#label_lookup = get_label_lookup(normalized_hu_feature_dict)

C:\Users\Animesh\AppData\Local\Temp\ipykernel_12188\1213881977.py:33: RuntimeWarning: invalid value encountered in double_scalars
  cr = m[0, 1] / m[0, 0]
C:\Users\Animesh\AppData\Local\Temp\ipykernel_12188\1213881977.py:34: RuntimeWarning: invalid value encountered in double_scalars
  cc = m[1, 0] / m[0, 0]
C:\Users\Animesh\AppData\Local\Temp\ipykernel_12188\2776015146.py:30: RuntimeWarning: invalid value encountered in double_scalars
  cr = m[0, 1] / m[0, 0]
C:\Users\Animesh\AppData\Local\Temp\ipykernel_12188\2776015146.py:31: RuntimeWarning: invalid value encountered in double_scalars
  cc = m[1, 0] / m[0, 0]


In [11]:
def get_flat_feature_list(hu_dict, nu_dict):
    feature_list = []
    keys = hu_dict.keys()
    for key in keys:
        num_vals = len(hu_dict.get(key))
        for i in range(num_vals):
            moments = list(hu_dict.get(key)[i])
            moments.extend(list(nu_dict.get(key)[i]))
            moments.append(key)
            feature_list.append(moments)
    return feature_list

In [12]:
import pandas as pd
from sklearn.preprocessing import MinMaxScaler
scaler = MinMaxScaler()
def process_train_test_data(hu_dict, nu_dict):
    # Create column names corresponding to each Hu Moment in DataFrame
    columns_hu = ["Hu" + str(i + 1) for i in range(7)]
    # Create column names corresponding to each Mu Moment in DataFrame
    #columns_mu = ["Mu" + str(i + 1) for i in range(16)]
    # Create column names corresponding to each Nu Moment in DataFrame
    columns_nu = ["Nu" + str(i + 1) for i in range(16)]
    # Columns
    cols = columns_hu + columns_nu
    cols.append("ClassID")
    # Create dataframe using training features
    df_train = pd.DataFrame(get_flat_feature_list(hu_dict, nu_dict), columns = cols)
                #.join(pd.DataFrame(get_flat_feature_list(nu_feature_dict), columns = columns_nu))
                #.join(pd.DataFrame(get_flat_feature_list(mu_feature_dict), columns = columns_mu))
                
    #df_train = pd.DataFrame(get_flat_feature_list(feature_dict), columns = columns)
    # Create dataframe using testing features
    #df_test = pd.DataFrame(get_flat_feature_list(test_hu_feature_dict), columns = columns_hu)\
    #        .join(pd.DataFrame(get_flat_feature_list(test_nu_feature_dict), columns = columns_nu))
            #.join(pd.DataFrame(get_flat_feature_list(test_mu_feature_dict), columns = columns_mu))
                

    # Combine train and test df for pre-processing
    #combined_df = pd.concat([df_train, df_test], ignore_index = True, sort = False)
    ## Drop NaN columns
    
    df_train.drop(["Nu1", "Nu2", "Nu5"], axis = 1, inplace = True)
    df_train.dropna(inplace=True)
    #print(df_train.head(25))
    # Scale data between 0 and 1
    columns = list(df_train.columns)
    columns.pop()
    print(columns)
    #scaler = MinMaxScaler()
    df_train[columns] = scaler.fit_transform(df_train[columns])
    print(df_train.head(25))
    #print(scaler.mean_)
    #df_train_scaled =minmax_scale(df_train)#.fit_transform(df_train)
    # Split scaled train and test dataframes
    #scaled_train_df = pd.DataFrame(combined_df[: len(df_train)])
    #scaled_test_df = pd.DataFrame(combined_df[len(df_train):])
    #scaled_test_df.reset_index(drop = True, inplace=True)
    #return (scaled_train_df, scaled_test_df)
    return df_train

In [13]:
df_train = process_train_test_data(train_hu_feature_dict, train_nu_feature_dict)
len(df_train)

['Hu1', 'Hu2', 'Hu3', 'Hu4', 'Hu5', 'Hu6', 'Hu7', 'Nu3', 'Nu4', 'Nu6', 'Nu7', 'Nu8', 'Nu9', 'Nu10', 'Nu11', 'Nu12', 'Nu13', 'Nu14', 'Nu15', 'Nu16']
             Hu1           Hu2           Hu3           Hu4           Hu5  \
2   5.336341e-03  2.788082e-05  2.109404e-07  2.136063e-07  4.728001e-10   
3   5.881688e-07  1.622755e-12  7.979929e-18  4.563388e-17  4.727548e-10   
6   5.336341e-03  2.788082e-05  2.109404e-07  2.136063e-07  4.728001e-10   
7   5.881688e-07  1.622755e-12  7.979929e-18  4.563388e-17  4.727548e-10   
8   3.182762e-04  7.791073e-08  2.711188e-11  3.743284e-11  4.727548e-10   
9   2.021641e-04  3.126868e-08  6.965449e-12  1.021883e-11  4.727548e-10   
10  8.408714e-06  9.767024e-12  7.437683e-17  5.232712e-17  4.727548e-10   
11  3.182762e-04  7.791073e-08  2.711188e-11  3.743284e-11  4.727548e-10   
12  2.021641e-04  3.126868e-08  6.965449e-12  1.021883e-11  4.727548e-10   
13  8.408714e-06  9.767024e-12  7.437683e-17  5.232712e-17  4.727548e-10   
14  2.406431e-04

12826

In [14]:
from sklearn.ensemble import RandomForestClassifier
X = df_train.iloc[:, :-1]
y = df_train.iloc[: , -1]
rfc = RandomForestClassifier(n_estimators = 500, n_jobs=-1).fit(X, y)

In [15]:
predicted_classes_dict = {}
for key, values in pred_feature_dict.items():
    for val in values:
        val = [item for i, item in enumerate(val) if i not in [7, 8, 11]]
        val = np.array(val)
        if np.isnan(val).any():
            continue
        val = val.reshape(1, -1)
        val = scaler.transform(val)
        predicted_classes_dict[key] = predicted_classes_dict.get(key, []) + [rfc.predict(val)]
#print(pred_feature_dict)

d:\Rutgers\Spring 2022\CS 534 - Computer Vision\Phase3\Logo-Detection-YOLOv2\dataset\FlickrLogos_47\env\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but MinMaxScaler was fitted with feature names
  warnings.warn(
d:\Rutgers\Spring 2022\CS 534 - Computer Vision\Phase3\Logo-Detection-YOLOv2\dataset\FlickrLogos_47\env\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
d:\Rutgers\Spring 2022\CS 534 - Computer Vision\Phase3\Logo-Detection-YOLOv2\dataset\FlickrLogos_47\env\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but MinMaxScaler was fitted with feature names
  warnings.warn(
d:\Rutgers\Spring 2022\CS 534 - Computer Vision\Phase3\Logo-Detection-YOLOv2\dataset\FlickrLogos_47\env\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestClassifier

In [16]:
predicted_classes_dict

{'000000704': [array(['24'], dtype=object),
  array(['11'], dtype=object),
  array(['45'], dtype=object),
  array(['12'], dtype=object)],
 '000001077': [array(['36'], dtype=object),
  array(['29'], dtype=object),
  array(['16'], dtype=object),
  array(['29'], dtype=object),
  array(['43'], dtype=object),
  array(['1'], dtype=object)],
 '000001690': [array(['29'], dtype=object),
  array(['12'], dtype=object),
  array(['10'], dtype=object),
  array(['32'], dtype=object)],
 '000002146': [array(['29'], dtype=object),
  array(['38'], dtype=object),
  array(['29'], dtype=object)],
 '000001915': [array(['1'], dtype=object)],
 '000001964': [array(['12'], dtype=object), array(['1'], dtype=object)],
 '000000293': [array(['12'], dtype=object)],
 '000001273': [array(['29'], dtype=object),
  array(['36'], dtype=object),
  array(['29'], dtype=object)],
 '000001319': [array(['29'], dtype=object)],
 '000000536': [array(['46'], dtype=object), array(['42'], dtype=object)],
 '000000346': [array(['29'], d

In [17]:
true_classes_dict = {}
for test_id in identifier_dict.get("test"):
    classes = []
    with open(os.path.join("rcnn_data", test_id + ".gt_data.txt")) as fp:
        for line in fp.readlines():
            classes.append(line.strip().split(" ")[4])
    true_classes_dict[test_id] = classes

In [18]:
true_classes_dict

{'000000704': ['13', '13', '14', '14'],
 '000001077': ['22', '22', '22', '22', '22', '22'],
 '000001690': ['36', '36', '36', '36'],
 '000002146': ['44', '45', '45'],
 '000001915': ['40'],
 '000001964': ['41', '42'],
 '000000293': ['5', '6'],
 '000001273': ['28', '28', '28'],
 '000000897': ['18'],
 '000001319': ['28'],
 '000000536': ['10', '11'],
 '000000346': ['5', '6'],
 '000001172': ['25'],
 '000000489': ['9', '9'],
 '000001464': ['29', '29', '29', '29'],
 '000000823': ['16', '16', '16', '16'],
 '000000162': ['3'],
 '000001412': ['0'],
 '000000189': ['3', '3', '3'],
 '000002101': ['44', '45'],
 '000000571': ['12'],
 '000001285': ['28', '28'],
 '000000579': ['12'],
 '000002053': ['43'],
 '000001459': ['29', '29', '29', '29'],
 '000001676': ['34',
  '34',
  '34',
  '34',
  '34',
  '34',
  '34',
  '34',
  '34',
  '34',
  '34',
  '34',
  '34',
  '34',
  '35',
  '35',
  '35',
  '35',
  '35',
  '35',
  '35',
  '35',
  '35',
  '35',
  '35',
  '35',
  '35',
  '35',
  '35'],
 '000001022': ['2

In [19]:
unraveled_pred_classes = {}
for key, val in predicted_classes_dict.items():
    unraveled_pred_classes[key] = list(np.ravel(val))

In [20]:
print(len(true_classes_dict)) 
print(len(unraveled_pred_classes))

1402
1378


In [21]:
unraveled_pred_classes

{'000000704': ['24', '11', '45', '12'],
 '000001077': ['36', '29', '16', '29', '43', '1'],
 '000001690': ['29', '12', '10', '32'],
 '000002146': ['29', '38', '29'],
 '000001915': ['1'],
 '000001964': ['12', '1'],
 '000000293': ['12'],
 '000001273': ['29', '36', '29'],
 '000001319': ['29'],
 '000000536': ['46', '42'],
 '000000346': ['29'],
 '000001172': ['29'],
 '000000489': ['36', '12'],
 '000001464': ['11', '9', '24', '29'],
 '000000823': ['29', '36', '36'],
 '000000162': ['24'],
 '000001412': ['29'],
 '000000189': ['34', '9', '35'],
 '000002101': ['29', '28'],
 '000000571': ['12'],
 '000001285': ['29'],
 '000000579': ['0'],
 '000002053': ['36'],
 '000001459': ['21', '36', '43', '36'],
 '000001676': ['36',
  '29',
  '43',
  '29',
  '12',
  '36',
  '35',
  '35',
  '29',
  '3',
  '24',
  '12',
  '11',
  '32',
  '43',
  '22',
  '36',
  '29',
  '37',
  '12',
  '30',
  '2',
  '15',
  '16',
  '34'],
 '000001022': ['20'],
 '000001699': ['6'],
 '000001719': ['21', '29', '36', '39', '29', '36'

In [22]:
def uniquify(temp_list):
    res = []
    for i, v in enumerate(temp_list):
        totalcount = temp_list.count(v)
        count = temp_list[:i].count(v)
        res.append(v + str(count + 1) if totalcount > 1 else v)
    return res

In [23]:
from sklearn.preprocessing import MultiLabelBinarizer
from sklearn.metrics import accuracy_score, precision_recall_fscore_support
mlb = MultiLabelBinarizer()
accuracy = []
for key in unraveled_pred_classes.keys():
    true_val = true_classes_dict.get(key)
    pred_val = unraveled_pred_classes.get(key)
    #true_val = uniquify(true_val)
    #pred_val = uniquify(pred_val)
    #print(key, true_val, pred_val)
    y_true, y_pred = mlb.fit_transform([true_val, pred_val])
    accuracy.append(accuracy_score(y_true, y_pred))
print(sum(accuracy) / len(accuracy))

0.037878109527665606


In [24]:
from sklearn.neural_network import MLPClassifier
mlp = MLPClassifier(random_state = 1, max_iter = 2500, hidden_layer_sizes=(100, 250, 500, 250, 100, )).fit(X, y)

In [25]:
mlp_predicted_classes_dict = {}
for key, values in pred_feature_dict.items():
    for val in values:
        val = [item for i, item in enumerate(val) if i not in [7, 8, 11]]
        val = np.array(val)
        if np.isnan(val).any():
            continue
        val = val.reshape(1, -1)
        val = scaler.transform(val)
        mlp_predicted_classes_dict[key] = mlp_predicted_classes_dict.get(key, []) + [mlp.predict(val)]

d:\Rutgers\Spring 2022\CS 534 - Computer Vision\Phase3\Logo-Detection-YOLOv2\dataset\FlickrLogos_47\env\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but MinMaxScaler was fitted with feature names
  warnings.warn(
d:\Rutgers\Spring 2022\CS 534 - Computer Vision\Phase3\Logo-Detection-YOLOv2\dataset\FlickrLogos_47\env\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but MLPClassifier was fitted with feature names
  warnings.warn(
d:\Rutgers\Spring 2022\CS 534 - Computer Vision\Phase3\Logo-Detection-YOLOv2\dataset\FlickrLogos_47\env\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but MinMaxScaler was fitted with feature names
  warnings.warn(
d:\Rutgers\Spring 2022\CS 534 - Computer Vision\Phase3\Logo-Detection-YOLOv2\dataset\FlickrLogos_47\env\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but MLPClassifier was fitted with f

In [26]:
mlp_unraveled_pred_classes = {}
for key, val in mlp_predicted_classes_dict.items():
    mlp_unraveled_pred_classes[key] = list(np.ravel(val))

In [27]:
mlp_accuracy = []
for key in mlp_unraveled_pred_classes.keys():
    true_val = true_classes_dict.get(key)
    pred_val = mlp_unraveled_pred_classes.get(key)
    #true_val = uniquify(true_val)
    #pred_val = uniquify(pred_val)
    #print(key, true_val, pred_val)
    y_true, y_pred = mlb.fit_transform([true_val, pred_val])
    mlp_accuracy.append(accuracy_score(y_true, y_pred))
print(sum(mlp_accuracy) / len(mlp_accuracy))

0.04126753749395259


In [28]:
import pandas as pd
df = pd.read_csv("./cosine/classifications.csv")

In [30]:
class_id_dict = {}
with open("./className2ClassID.txt") as fp:
    lines = fp.readlines()
    for line in lines:
        line.strip()
        key, val = line.split("\t")
        val = val.strip("\n")
        class_id_dict[key] = val
class_id_dict

{'HP': '0',
 'adidas_symbol': '1',
 'adidas_text': '2',
 'aldi': '3',
 'apple': '4',
 'becks_symbol': '5',
 'becks_text': '6',
 'bmw': '7',
 'carlsberg_symbol': '8',
 'carlsberg_text': '9',
 'chimay_symbol': '10',
 'chimay_text': '11',
 'cocacola': '12',
 'corona_symbol': '13',
 'corona_text': '14',
 'dhl': '15',
 'erdinger_symbol': '16',
 'erdinger_text': '17',
 'esso_symbol': '18',
 'esso_text': '19',
 'fedex': '20',
 'ferrari': '21',
 'ford': '22',
 'fosters_symbol': '23',
 'fosters_text': '24',
 'google': '25',
 'guinness_symbol': '26',
 'guinness_text': '27',
 'heineken': '28',
 'milka': '29',
 'nvidia_symbol': '30',
 'nvidia_text': '31',
 'paulaner_symbol': '32',
 'paulaner_text': '33',
 'pepsi_symbol': '34',
 'pepsi_text': '35',
 'rittersport': '36',
 'shell': '37',
 'singha_symbol': '38',
 'singha_text': '39',
 'starbucks': '40',
 'stellaartois_symbol': '41',
 'stellaartois_text': '42',
 'texaco': '43',
 'tsingtao_symbol': '44',
 'tsingtao_text': '45',
 'ups': '46'}

In [31]:
def get_proper_class(pred):
    if "Guiness" in pred:
        pred = pred.replace("Guiness", "guinness")
    pred = pred.replace("'", "").replace(" ", "").replace("(", "_").replace(")", "").replace("-", "").lower()
    if pred == "hp":
        pred = "HP"
    return pred

In [32]:
pred_set = set()
class_set = set()
cosine_preds = {}
for i, row in df.iterrows():
    key = row["image_file"].split("/")[-1][:-4]
    class_set.add(row["classification"])
    prediction = get_proper_class(row["classification"])
    pred_set.add(prediction)
    if prediction == "":
        continue
    val = class_id_dict.get(prediction)
    cosine_preds[key] = cosine_preds.get(key, []) + [val]

In [33]:
pred_set, class_set

({'',
  'HP',
  'adidas_symbol',
  'adidas_text',
  'aldi',
  'apple',
  'becks_symbol',
  'becks_text',
  'bmw',
  'carlsberg_symbol',
  'carlsberg_text',
  'chimay_text',
  'cocacola',
  'corona_symbol',
  'corona_text',
  'dhl',
  'erdinger_symbol',
  'erdinger_text',
  'esso_symbol',
  'esso_text',
  'fedex',
  'ferrari',
  'ford',
  'fosters_symbol',
  'fosters_text',
  'guinness_symbol',
  'guinness_text',
  'heineken',
  'milka',
  'nvidia_symbol',
  'nvidia_text',
  'paulaner_symbol',
  'paulaner_text',
  'pepsi_symbol',
  'pepsi_text',
  'rittersport',
  'shell',
  'stellaartois_symbol',
  'stellaartois_text',
  'tsingtao_symbol',
  'tsingtao_text',
  'ups'},
 {'-',
  'BMW',
  'Chimay (Text)',
  'Coca-Cola',
  'Corona (Symbol)',
  'Corona (Text)',
  'DHL',
  'Erdinger (Symbol)',
  'Erdinger (Text)',
  'Esso (Symbol)',
  'Esso (Text)',
  'Fedex',
  'Ferrari',
  'Ford',
  "Foster's (Symbol)",
  "Foster's (Text)",
  'Guiness (Symbol)',
  'Guiness (Text)',
  'HP',
  'Heineken',
  

In [34]:
cosine_preds

{'000000000': ['46', '46', '23'],
 '000000001': ['22', '19', '23', '23'],
 '000000002': ['46', '20', '7'],
 '000000003': ['46',
  '7',
  '46',
  '23',
  '46',
  '46',
  '46',
  '23',
  '3',
  '28',
  '34',
  '26',
  '46',
  '46',
  '46'],
 '000000004': ['19', '9', '23'],
 '000000005': ['8', '46', '27', '46', '23'],
 '000000006': ['9',
  '23',
  '9',
  '46',
  '23',
  '46',
  '3',
  '46',
  '46',
  '46',
  '45',
  '34',
  '46'],
 '000000008': ['23', '3', '23', '9'],
 '000000009': ['22', '23'],
 '000000011': ['23', '46'],
 '000000012': ['36', '24', '9', '8', '46', '45', '23'],
 '000000013': ['23'],
 '000000016': ['26', '0', '34', '3', '23'],
 '000000018': ['19', '3', '32', '9', '46'],
 '000000021': ['3', '3', '23'],
 '000000023': ['12', '23'],
 '000000024': ['46', '46', '46', '46'],
 '000000026': ['34', '46', '24'],
 '000000027': ['19', '46', '22'],
 '000000029': ['3', '19', '46', '46'],
 '000000030': ['23', '26', '46', '23', '7', '3', '3', '3'],
 '000000031': ['35', '23', '17', '23', '4

In [35]:
cosine_accuracy = []
for key in cosine_preds.keys():
    true_val = true_classes_dict.get(key)
    pred_val = cosine_preds.get(key)
    #true_val = uniquify(true_val)
    #pred_val = uniquify(pred_val)
    #print(key, true_val, pred_val)
    y_true, y_pred = mlb.fit_transform([true_val, pred_val])
    cosine_accuracy.append(accuracy_score(y_true, y_pred))
print(sum(cosine_accuracy) / len(cosine_accuracy))

0.22565095700944737
